
# Parameter space

In this example,
we will see the basics of :class:`.ParameterSpace`.


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo.algos.parameter_space import ParameterSpace
from gemseo.post.dataset.scatter_plot_matrix import ScatterMatrix

configure_logger()

## Create a parameter space
Firstly,
the creation of a :class:`.ParameterSpace` does not require any mandatory argument:



In [ ]:
parameter_space = ParameterSpace()

Then, we can add either deterministic variables
from their lower and upper bounds
(use :meth:`.ParameterSpace.add_variable`):



In [ ]:
parameter_space.add_variable("x", l_b=-2.0, u_b=2.0)

or uncertain variables from their distribution names and parameters
(use :meth:`.ParameterSpace.add_random_variable`):



In [ ]:
parameter_space.add_random_variable("y", "SPNormalDistribution", mu=0.0, sigma=1.0)
parameter_space

<div class="alert alert-danger"><h4>Warning</h4><p>We cannot mix probability distributions from different families,
   e.g. an :class:`.OTDistribution` and a :class:`.SPDistribution`.</p></div>

We can check that the variables *x* and *y* are implemented
as deterministic and uncertain variables respectively:



In [ ]:
parameter_space.is_deterministic("x"), parameter_space.is_uncertain("y")

Note that when GEMSEO does not offer a class for the SciPy distribution,
we can use the generic GEMSEO class :class:`.SPDistribution`
to create any SciPy distribution
by setting ``interfaced_distribution`` to its SciPy name
and ``parameters`` as a dictionary of SciPy parameter names and values
([see the documentation of SciPy](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.norm.html)_).



In [ ]:
# parameter_space.add_random_variable(
#     "y",
#     "SPDistribution",
#     interfaced_distribution="norm",
#     parameters={"loc": 1.0, "scale": 2.0},
# )

A similar procedure can be followed
for OpenTURNS distributions for which
GEMSEO does not offer a class directly.
We can use the generic GEMSEO class :class:`.OTDistribution`
to create any OpenTURNS distribution
by setting ``interfaced_distribution`` to its OpenTURNS name
and ``parameters`` as a tuple of OpenTURNS parameter values
([see the documentation of OpenTURNS](https://openturns.github.io/openturns/latest/user_manual/_generated/
openturns.Normal.html#openturns.Normal)_).



In [ ]:
# parameter_space.add_random_variable(
#     "y",
#     "OTDistribution",
#     interfaced_distribution="Normal",
#     parameters=(1.0, 2.0),
# )

## Sample from the parameter space
We can sample the uncertain variables from the :class:`.ParameterSpace`
and get values either as a NumPy array (by default)



In [ ]:
sample = parameter_space.compute_samples(n_samples=2, as_dict=True)
sample

or as a dictionary of NumPy arrays indexed by the names of the variables:



In [ ]:
sample = parameter_space.compute_samples(n_samples=4)
sample

## Sample a discipline over the parameter space
We can also sample a discipline over the parameter space.
For simplicity,
we instantiate an :class:`.AnalyticDiscipline` from a dictionary of expressions:



In [ ]:
discipline = create_discipline("AnalyticDiscipline", expressions={"z": "x+y"})

From these parameter space and discipline,
we build a :class:`.DOEScenario`
and execute it with a Latin Hypercube Sampling algorithm and 100 samples.

<div class="alert alert-danger"><h4>Warning</h4><p>A :class:`.DOEScenario` considers all the variables
   available in its :class:`.DesignSpace`.
   By inheritance,
   in the special case of a :class:`.ParameterSpace`,
   a :class:`.DOEScenario` considers all the variables
   available in this :class:`.ParameterSpace`.
   Thus,
   if we do not filter the uncertain variables,
   the :class:`.DOEScenario` will consider
   both the deterministic variables as uniformly distributed variables
   and the uncertain variables with their specified probability distributions.</p></div>



In [ ]:
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "z", parameter_space, scenario_type="DOE"
)
scenario.execute({"algo": "lhs", "n_samples": 100})

We can export the optimization problem to a :class:`.Dataset`:



In [ ]:
dataset = scenario.to_dataset(name="samples")

and visualize it in a tabular way:



In [ ]:
dataset

or with a graphical post-processing,
e.g. a scatter plot matrix:



In [ ]:
ScatterMatrix(dataset).execute(save=False, show=True)

## Sample a discipline over the uncertain space
If we want to sample a discipline over the uncertain space,
we need to extract it:



In [ ]:
uncertain_space = parameter_space.extract_uncertain_space()

Then, we clear the cache, create a new scenario from this parameter space
containing only the uncertain variables and execute it.



In [ ]:
scenario = create_scenario(
    [discipline], "DisciplinaryOpt", "z", uncertain_space, scenario_type="DOE"
)
scenario.execute({"algo": "lhs", "n_samples": 100})

Finally,
we build a dataset from the disciplinary cache and visualize it.
We can see that the deterministic variable 'x' is set to its default value
for all evaluations,
contrary to the previous case where we were considering the whole parameter space:



In [ ]:
dataset = scenario.to_dataset(name="samples")
dataset